<a href="https://colab.research.google.com/github/setthawut8/ai/blob/main/s2t/%5Basr%26tts%5D_library_comparison.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#wav data

In [61]:
%%capture
#sale audio
!gdown 1kfbV9yiRInOvj6AHw9dlCdiJpGpmoVEm
!unzip 'voice_data.zip'

#hell where i am audio
!gdown 1BS-k09RcB5Ulrau0Fpc_FOPoyKzXkj7p

In [62]:
import os
import wave
import glob
import IPython

#data

In [63]:
#get all voice paths
all_wavs = glob.glob('/content/voice data/*.wav')
all_wavs

#open the wave file
audio_file = all_wavs[-1]

IPython.display.Audio(audio_file)

#check audio parameters

In [65]:
#check sample rate/ frame rate
import wave
import IPython

#open the wave file
filepath = '/content/hi_where_am_i.wav'
obj = wave.open(filepath, "rb")
IPython.display.Audio(filepath)

#get audio signal parameters
print("# of channels ", obj.getnchannels())
print("sample width ", obj.getsampwidth())
print("frame rate ", obj.getframerate())
print("# of frames ", obj.getnframes())
print("parameters ", obj.getparams())

# of channels  1
sample width  4
frame rate  48000
# of frames  236160
parameters  _wave_params(nchannels=1, sampwidth=4, framerate=48000, nframes=236160, comptype='NONE', compname='not compressed')


#record speeches
https://colab.research.google.com/drive/1zHt3GoxXWCaNSMRzE5lrvpYm9RolcxOW?usp=sharing#scrollTo=5fn-nJy8v2Dc

In [ ]:
%%capture
!pip install pydub
!pip install --upgrade gupload

In [ ]:
from pydrive.auth import GoogleAuth
from google.colab import auth


# Authenticate and create the PyDrive client.
auth.authenticate_user()

# if multiple images
# !gupload --to '1wNJUZtQD_6oBvvUhWRlAb0xjjjoLZQ' *.png

In [ ]:
from pythaiasr import asr
from IPython.display import Javascript
from google.colab import output as colab_output
from io import BytesIO
from base64 import b64decode
from pydub import AudioSegment
import os.path
import time

RECORD = """
const sleep  = time => new Promise(resolve => setTimeout(resolve, time))
const b2text = blob => new Promise(resolve => {
  const reader = new FileReader()
  reader.onloadend = e => resolve(e.srcElement.result)
  reader.readAsDataURL(blob)
})
var record = time => new Promise(async resolve => {
  stream = await navigator.mediaDevices.getUserMedia({ audio: true })
  recorder = new MediaRecorder(stream)
  chunks = []
  recorder.ondataavailable = e => chunks.push(e.data)
  recorder.start()
  await sleep(time)
  recorder.onstop = async ()=>{
    blob = new Blob(chunks)
    text = await b2text(blob)
    resolve(text)
  }
  recorder.stop()
})
"""

def record(seconds=5):
    display(Javascript(RECORD))
    print(f"Recording started for {seconds} seconds.")
    s = colab_output.eval_js("record(%d)" % (seconds * 1000))
    print("Recording ended.")
    b = b64decode(s.split(",")[1])

    file_name = 'hi_where_am_i'
    fileformat = "wav"
    filename = str(f"{file_name}.{fileformat}")
    
    #save audio file
    AudioSegment.from_file(BytesIO(b)).export(filename, format=fileformat)

    #upload file to gdrive

    return asr(filename), filename

In [ ]:
asr_results, filename = record()
asr_results, filename

<IPython.core.display.Javascript object>

Recording started for 5 seconds.
Recording ended.
Uploading file: hi_where_am_i.wav


/usr/local/lib/python3.7/dist-packages/transformers/configuration_utils.py:369: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  "Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 "
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.


('สวัส ดีก ครับ   ปัน นี้ ทิน ข้าว เซ็ท   กำลัง เขียน โขด ครับ',
 'hi_where_am_i.wav')

#speech recognition (SR)

##pythaiasr
https://github.com/PyThaiNLP/pythaiasr

In [66]:
#uninstall tensorflow so we can use pythaiasr 
!pip uninstall tensorflow -y
!pip install pythaiasr

In [67]:
filepath = '/content/hi_where_am_i.wav'

In [68]:
import IPython
from pythaiasr import asr

In [69]:
#open the wave file
IPython.display.Audio(filepath)

In [70]:
#asr
asr(filepath)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.


'สวัส ดีก ครับ   ปัน นี้ ทิน ข้าว เซ็ท   กำลัง เขียน โขด ครับ'

##speech recognition (google)
tutorial
https://www.youtube.com/watch?v=xuafxNcFsiE

each type of library
https://github.com/Uberi/speech_recognition/blob/master/examples/audio_transcribe.py

In [ ]:
!pip install SpeechRecognition

In [72]:
import IPython
import speech_recognition as sr

In [73]:
filepath = '/content/hi_where_am_i.wav'

#initialize the library
r = sr.Recognizer()

general_hi = sr.AudioFile(filepath)
with general_hi as source:
  audio = r.record(source)

print(type(audio))

#open the wave file
IPython.display.Audio(filepath)

<class 'speech_recognition.AudioData'>


In [74]:
#language based on RFC5646 language tag (https://gist.github.com/msikma/8912e62ed866778ff8cd)
google_text_0 = r.recognize_google(audio, language='th') #Google Speech Recognition
print("Google Speech Recognition: ", google_text)

Google Speech Recognition:  สวัสดีครับตอนนี้กินข้าวเสร็จกำลังจะนอนครับ


#text to speech (TTS)

In [75]:
%%capture
!pip install gTTS

In [76]:
#list all languages: {"Thai: th"}
!gtts-cli --all

  af: Afrikaans
  ar: Arabic
  bg: Bulgarian
  bn: Bengali
  bs: Bosnian
  ca: Catalan
  cs: Czech
  cy: Welsh
  da: Danish
  de: German
  el: Greek
  en: English
  eo: Esperanto
  es: Spanish
  et: Estonian
  fi: Finnish
  fr: French
  gu: Gujarati
  hi: Hindi
  hr: Croatian
  hu: Hungarian
  hy: Armenian
  id: Indonesian
  is: Icelandic
  it: Italian
  iw: Hebrew
  ja: Japanese
  jw: Javanese
  km: Khmer
  kn: Kannada
  ko: Korean
  la: Latin
  lv: Latvian
  mk: Macedonian
  ml: Malayalam
  mr: Marathi
  ms: Malay
  my: Myanmar (Burmese)
  ne: Nepali
  nl: Dutch
  no: Norwegian
  pl: Polish
  pt: Portuguese
  ro: Romanian
  ru: Russian
  si: Sinhala
  sk: Slovak
  sq: Albanian
  sr: Serbian
  su: Sundanese
  sv: Swedish
  sw: Swahili
  ta: Tamil
  te: Telugu
  th: Thai
  tl: Filipino
  tr: Turkish
  uk: Ukrainian
  ur: Urdu
  vi: Vietnamese
  zh-CN: Chinese
  zh-TW: Chinese (Mandarin/Taiwan)
  zh: Chinese (Mandarin)


In [77]:
from gtts import gTTS
tts = gTTS('สวัสดี', lang='th')
tts.save('hello1.wav')

In [78]:
IPython.display.Audio('/content/hello1.wav')